In [1]:
import pandas as pd
import plotly.express as px

In [2]:
# Importar dataset y revisar datos
boardgames_data = pd.read_csv('../datasets/boardgames_ranks.csv')
boardgames_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 151733 entries, 0 to 151732
Data columns (total 15 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   id                   151733 non-null  int64  
 1   name                 151733 non-null  object 
 2   yearpublished        151733 non-null  int64  
 3   rank                 151733 non-null  int64  
 4   bayesaverage         151733 non-null  float64
 5   average              151733 non-null  float64
 6   usersrated           151733 non-null  int64  
 7   abstracts_rank       1408 non-null    float64
 8   cgs_rank             347 non-null     float64
 9   childrensgames_rank  1044 non-null    float64
 10  familygames_rank     3114 non-null    float64
 11  partygames_rank      878 non-null     float64
 12  strategygames_rank   2867 non-null    float64
 13  thematic_rank        1590 non-null    float64
 14  wargames_rank        4176 non-null    float64
dtypes: float64(10), i

In [3]:
boardgames_data.sample(10)

id                                       name  yearpublished  \
37212    19741                      Blue Moon: The Pillar           2005   
7825     27306                                    Venedig           2007   
28544     7438  Adventures with Clifford, the Big Red Dog           1992   
3159      6866                                        Mus           1745   
35862    17968                       N30: We Are Winning!           2004   
65598    97470                                    Jarmial           2010   
109994  273920                  Djinns of the High Desert           2019   
115382  294777           Black Powder: Glory, Hallelujah!           2016   
42258    26225                                     Caroti           2006   
147388  399751                       Maailmanpelastuspeli           2019   

        rank  bayesaverage  average  usersrated  abstracts_rank  cgs_rank  \
37212      0       5.93685  7.21418         684             NaN       NaN   
7825    7826       5.61099  6.27135         356             NaN       NaN   
28544      0       0.00000  4.00000           1             NaN       NaN   
3159    3160       5.94719  7.94853         495             NaN       NaN   
35862      0       0.00000  6.75000           2             NaN       NaN   
65598      0       0.00000  6.41429           7             NaN       NaN   
109994     0       0.00000  7.43750           8             NaN       NaN   
115382     0       0.00000  6.61111           9             NaN       NaN   
42258      0       0.00000  4.70000           3             NaN       NaN   
147388     0       0.00000  6.00000           2             NaN       NaN   

        childrensgames_rank  familygames_rank  partygames_rank  \
37212                   NaN               NaN              NaN   
7825                    NaN               NaN              NaN   
28544                   NaN               NaN              NaN   
3159                    NaN             882.0              NaN   
35862                   NaN               NaN              NaN   
65598                   NaN               NaN              NaN   
109994                  NaN               NaN              NaN   
115382                  NaN               NaN              NaN   
42258                   NaN               NaN              NaN   
147388                  NaN               NaN              NaN   

        strategygames_rank  thematic_rank  wargames_rank  
37212                  NaN            NaN            NaN  
7825                   NaN            NaN            NaN  
28544                  NaN            NaN            NaN  
3159                   NaN            NaN            NaN  
35862                  NaN            NaN            NaN  
65598                  NaN            NaN            NaN  
109994                 NaN            NaN            NaN  
115382                 NaN            NaN            NaN  
42258                  NaN            NaN            NaN  
147388                 NaN            NaN            NaN

In [4]:
# Contar cuantos juegos no posee año de publicación
bg_no_year_count = boardgames_data[boardgames_data['yearpublished'] == 0]['id'].count()
print(f'Hay un total de {bg_no_year_count} juegos sin año de publicación')

Hay un total de 11325 juegos sin año de publicación


## Preparación de datos
Existen varias filas que no presentan Año de lanzamiento ni ranking, para este caso, además muchos ranking por categoria son nulos, estos se utilizaran para obtener las categorias de cada juego. Aun que para este analisis de omitiran las filas que no presenten año.

In [5]:

boardgames_data = boardgames_data[((boardgames_data['yearpublished'] != 0))]

In [83]:
boardgames_data.sample(5, random_state=35)

id                                name  yearpublished   rank  \
135585  358123       Solitaire Legends: Tiger Lily           2022      0   
24563    18574                          Dark Force           1994  24564   
26519     3260                         Gaukelspiel           1998      0   
2845    283797  Exit: The Game – The Stormy Flight           2019   2846   
7191      1202                 The Sorcerer's Cave           1978   7192   

        bayesaverage  average  usersrated  abstracts_rank  cgs_rank  \
135585       0.00000  6.62500           8             NaN       NaN   
24563        5.47262  4.43455          55             NaN     328.0   
26519        0.00000  6.28571          21             NaN       NaN   
2845         5.99892  6.82805        1263             NaN       NaN   
7191         5.62961  6.48285         393             NaN       NaN   

        childrensgames_rank  familygames_rank  partygames_rank  \
135585                  NaN               NaN              NaN   
24563                   NaN               NaN              NaN   
26519                   NaN               NaN              NaN   
2845                    NaN               NaN              NaN   
7191                    NaN            1916.0              NaN   

        strategygames_rank  thematic_rank  wargames_rank   category  
135585                 NaN            NaN            NaN  undefined  
24563                  NaN            NaN            NaN     Cartas  
26519                  NaN            NaN            NaN  undefined  
2845                   NaN          512.0            NaN   Tematico  
7191                   NaN         1064.0            NaN    Familia

In [7]:
def categorize_game(game):
    category = 'undefined'
    categories = {
        'abstracts_rank' : 'Abstractos',
        'cgs_rank' : 'Cartas',
        'childrensgames_rank' : 'Niños',
        'familygames_rank' : 'Familia',
        'partygames_rank' : 'Fiesta',
        'strategygames_rank' : 'Estrategia',
        'thematic_rank' : 'Tematico',
        'wargames_rank' : 'De guerra'
    }
    rank_cat = 0
    for category_rank in categories.keys():
        if (not pd.isna(game[category_rank]) and category == 'undefined'):
            category = categories[category_rank]
            rank_cat = game[category_rank]
        elif not pd.isna(game[category_rank]):
            if game[category_rank] > rank_cat:
                category = categories[category_rank]
                rank_cat = game[category_rank]
    return category


In [8]:
boardgames_data['category'] = boardgames_data.apply(categorize_game, axis=1)

In [85]:
# Creación histograma
fig = px.histogram(
    boardgames_data[boardgames_data['average'] != 0], 
    x='average', nbins=20, 
    color='category',
    labels=dict(average="Puntucación promedio", category='Categorias')
)
fig.show()

/home/jcardoso/projects/python/tripleten_ds/sprint_5/tripleten_ds_sprint_5_proyecto/.env/lib/python3.10/site-packages/plotly/express/_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



In [86]:
# Diagrama de barras

#Filtrar para eliminar undefined
bg_category_filtered = boardgames_data[boardgames_data['category']!='undefined']['category']
category_counts = bg_category_filtered.value_counts()
fig = px.bar(
    x=category_counts.index, 
    y=category_counts.values, 
    labels={'x':'Categoría', 'y':'Cantidad de juegos'}
)
fig.show()

In [95]:
# Grafico de barras

# Filtrar juegos publicados despues de 1950 cuya categoria no sea indefinido
filtered_data = boardgames_data[(boardgames_data['yearpublished'] >= 1950)]

# Creacion de 
grouped_data = filtered_data.groupby(['yearpublished', 'category']).size().reset_index(name='count')


fig = px.bar(grouped_data, x='yearpublished', y='count', color='category',
             labels={'count': 'Número de Juegos', 'yearpublished': 'Año', 'category':'Categoria'},
             title='Expansión de juegos de mesa en el tiempo')
fig.show()

/home/jcardoso/projects/python/tripleten_ds/sprint_5/tripleten_ds_sprint_5_proyecto/.env/lib/python3.10/site-packages/plotly/express/_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



In [99]:
# Grafico de dispersión
fig = px.scatter(
    boardgames_data, 
    x="average", 
    y="usersrated",
    title='Relación puntuación/numero de votos',
    labels={'usersrated':'Cantidad de votos', 'average':'Puntucación promedio'}
) 
fig.show()

In [104]:
#Filtrar juegos que esten dentro del ranking
filtered_data = boardgames_data[boardgames_data['rank'] != 0]
fig = px.scatter(
    filtered_data, 
    x="rank", 
    y="average", 
    color='category',
    title='Como se relaciona el ranking de un juego con su puntuacion',
    labels={'rank':'Lugar en el ranking', 'average':'Puntuación promedio'})
fig.show()

/home/jcardoso/projects/python/tripleten_ds/sprint_5/tripleten_ds_sprint_5_proyecto/.env/lib/python3.10/site-packages/plotly/express/_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.

